<a href="https://colab.research.google.com/github/leofengg/Spotify-Song-Recommender/blob/main/SpotifyRecommender.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import pandas as pd

from sklearn import preprocessing

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

import seaborn as sns
import matplotlib.pyplot as plt

from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.manifold import TSNE
from sklearn.decomposition import PCA
from sklearn.metrics import euclidean_distances
from scipy.spatial.distance import cdist

In [ ]:
# dataframe = pd.read_csv('dataset.csv')
# dataframe.head()

In [ ]:
from google.colab import drive
drive.mount("/content/drive")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
dataframe = pd.read_csv("drive/My Drive/dataset.csv")

In [ ]:
new_df = dataframe.drop(columns=['time_signature', 'Unnamed: 0', 'key'])
new_df.drop_duplicates(subset=['track_id'], inplace=True)
new_df.drop_duplicates(subset=['artists', 'track_name'], inplace=True)
new_df.head()

track_id                 artists  \
0  5SuOikwiRyPMVoIQDJUgSV             Gen Hoshino   
1  4qPNDBW1i3p13qLCt0Ki3A            Ben Woodward   
2  1iJBSr7s7jYXzM8EGcbK5b  Ingrid Michaelson;ZAYN   
3  6lfxq3CG4xtTiEg7opyCyx            Kina Grannis   
4  5vjLSffimiIP26QG5WcN2K        Chord Overstreet   

                                          album_name  \
0                                             Comedy   
1                                   Ghost (Acoustic)   
2                                     To Begin Again   
3  Crazy Rich Asians (Original Motion Picture Sou...   
4                                            Hold On   

                   track_name  popularity  duration_ms  explicit  \
0                      Comedy          73       230666     False   
1            Ghost - Acoustic          55       149610     False   
2              To Begin Again          57       210826     False   
3  Can't Help Falling In Love          71       201933     False   
4                     Hold On          82       198853     False   

   danceability  energy  loudness  mode  speechiness  acousticness  \
0         0.676  0.4610    -6.746     0       0.1430        0.0322   
1         0.420  0.1660   -17.235     1       0.0763        0.9240   
2         0.438  0.3590    -9.734     1       0.0557        0.2100   
3         0.266  0.0596   -18.515     1       0.0363        0.9050   
4         0.618  0.4430    -9.681     1       0.0526        0.4690   

   instrumentalness  liveness  valence    tempo track_genre  
0          0.000001    0.3580    0.715   87.917    acoustic  
1          0.000006    0.1010    0.267   77.489    acoustic  
2          0.000000    0.1170    0.120   76.332    acoustic  
3          0.000071    0.1320    0.143  181.740    acoustic  
4          0.000000    0.0829    0.167  119.949    acoustic

In [ ]:
# scaler = preprocessing.MinMaxScaler()
# songs = new_df.select_dtypes(include=np.number).columns
# d = scaler.fit_transform(new_df.select_dtypes(include=np.number))
# normalized_data = pd.DataFrame(d, columns=songs)
# normalized_data.set_index(new_df.loc[:, 'track_id'], inplace=True)

# normalized_data

CHOOSING A TRACK

In [ ]:
# track = list(normalized_data.iloc[17])
# track

CLUSTERING

In [ ]:
from sklearn.cluster import KMeans
pipeline = Pipeline([('scaler', StandardScaler()), ('kmeans', KMeans(n_clusters=10))])
X = new_df.select_dtypes(np.number)
print(X.columns)
num_cols = list(X.columns)
pipeline.fit(X)


prediction = pipeline.predict(X)
new_df['cluster_label'] = prediction

Index(['popularity', 'duration_ms', 'danceability', 'energy', 'loudness',
       'mode', 'speechiness', 'acousticness', 'instrumentalness', 'liveness',
       'valence', 'tempo'],
      dtype='object')


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [ ]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import plotly.express as px

pca_pipeline = Pipeline([('scaler', StandardScaler()), ('PCA', PCA(n_components=2))])

song_embedding = pca_pipeline.fit_transform(X)

projection = pd.DataFrame(columns=['x', 'y'], data=song_embedding)
projection['title'] = new_df['track_name']
projection['cluster'] = new_df['cluster_label']

figure = px.scatter(
    projection, x='x', y='y', color='cluster', hover_data=['x', 'y', 'title']
    )
figure.show()

RECOMMENDER

In [ ]:
!pip install spotipy
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
clientId = "116324ccdd2d4685949902b3a8e42911"
clientSecret = "f86c15a412564ef48ea45aaa50ee7c31"
clientCredentialsManager = SpotifyClientCredentials(client_id = clientId, client_secret = clientSecret)
s = spotipy.Spotify(client_credentials_manager = clientCredentialsManager)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from collections import defaultdict

def find_song(name, artists):
  song_data = defaultdict()
  result = s.search(q='track: {} artist {}'.format(name, artists,), limit=1)
  if result['tracks']['items'] == []:
    return None

  result = result['track']['items'][0]
  track_id = result['id']
  features = s.audio_features(track_id)[0]

  song_data['name'] = [name]
  song_data['artists'] = [artists]
  song_data['explicit'] = [int(result['explicit'])]
  song_data['duration_ms'] = [result['duration_ms']]
  song_data['popularity'] = [result['popularity']]

  for key, value in features.items():
    song_data[key] = value

  return pd.DataFrame(song_data)


In [ ]:
from pandas._libs.tslibs.fields import get_date_name_field
from collections import defaultdict
from sklearn.metrics import euclidean_distances
from scipy.spatial.distance import cdist
import difflib

# cols = ["track_id",	"artists",	"album_name",	"track_name",	"popularity",	"duration_ms",
#         "explicit",	"danceability",	"energy",	"loudness",	"mode",	"speechiness",	"acousticness",	"instrumentalness",	"liveness",	"valence",	"tempo",	"track_genre"]
cols = ['popularity', 'duration_ms', 'danceability', 'energy', 'loudness',
       'mode', 'speechiness', 'acousticness', 'instrumentalness', 'liveness',
       'valence', 'tempo']


def get_data(song, data):
  try:
    song_data = data[(data['track_name'] == song['track_name']) & (data['artists'] == song['artists'])]
    return song_data
  except IndexError:
    return find_song(song['track_name'], song['artists'])

def get_mean_vector(song_list, spotify_data):

    song_vectors = []

    for song in song_list:
        song_data = get_data(song, spotify_data)
        if song_data is None:
            print('Warning: {} does not exist in Spotify or in database'.format(song['track_name']))
            continue
        song_vector = song_data[cols].values
        song_vectors.append(song_vector)

    song_matrix = np.array((song_vectors))
    return np.mean(song_matrix, axis=0)

def flatten_dict_list(dict_list):

  res = defaultdict()

  for key in dict_list[0].keys():
    res[key] = []

  for dictionary in dict_list:
    for key, value in dictionary.items():
      res[key].append(value)

  return res

def recommend_songs(song_list, spotify_data, model, n_songs=10):

  metadata_cols = ['track_name', 'artists']
  song_dict = flatten_dict_list(song_list)

  song_center = get_mean_vector(song_list, spotify_data)
  scaler = model.steps[0][1]
  scaled_data = scaler.transform(spotify_data[cols])
  scaled_song_center = scaler.transform(song_center.reshape(1, -1))
  distances = cdist(scaled_song_center, scaled_data, 'cosine')
  index = list(np.argsort(distances)[:, :n_songs][0])

  rec_songs = spotify_data.iloc[index]
  rec_songs = rec_songs[~rec_songs['track_name'].isin(song_dict['track_name'])]

  return rec_songs[metadata_cols].to_dict(orient='records')



In [ ]:
recommend_songs([{'track_name': 'Unstoppable', 'artists': 'Sia'},
                {'track_name': 'Cheap Thrills', 'artists': 'Sia'},
                {'track_name': 'Levitating', 'artists': 'Dua Lipa'},
                {'track_name': 'TFW (That Feeling When)', 'artists': 'ENHYPEN'},],  new_df, pipeline)

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names



[{'track_name': 'Summer', 'artists': 'Calvin Harris'},
 {'track_name': 'Dynamite', 'artists': 'BTS'},
 {'track_name': 'Sugar (feat. Francesco Yates)',
  'artists': 'Robin Schulz;Francesco Yates'},
 {'track_name': 'Boy With Luv (feat. Halsey)', 'artists': 'BTS;Halsey'},
 {'track_name': 'Fluorescent Adolescent', 'artists': 'Arctic Monkeys'},
 {'track_name': 'LO$ER=LO♡ER', 'artists': 'TOMORROW X TOGETHER'},
 {'track_name': 'Levitating (feat. DaBaby)', 'artists': 'Dua Lipa;DaBaby'},
 {'track_name': 'DNA', 'artists': 'BTS'},
 {'track_name': 'Bad Memories (feat. Elley Duhé & FAST BOY)',
  'artists': 'MEDUZA;James Carter;Elley Duhé;FAST BOY'},
 {'track_name': 'Blue Hour', 'artists': 'TOMORROW X TOGETHER'}]